# Gensim Word2Vec με τους Simpsons

# Ξεκινώντας

## Ρύθμιση του περιβάλλοντος

Βιβλιοθήκες:
 *  `xlrd` https://pypi.org/project/xlrd/
 * `spaCy` https://spacy.io/usage/
 * `gensim` https://radimrehurek.com/gensim/install.html
 * `scikit-learn` http://scikit-learn.org/stable/install.html
 * `seaborn` https://seaborn.pydata.org/installing.html

In [1]:
import re  # For preprocessing
import pandas as pd  # For data handling
from time import time  # To time our operations
from collections import defaultdict  # For word frequency

import spacy  # For preprocessing

import logging  # Setting up the loggings to monitor gensim
logging.basicConfig(format="%(levelname)s - %(asctime)s: %(message)s", datefmt= '%H:%M:%S', level=logging.INFO)

<img src="https://upload.wikimedia.org/wikipedia/commons/4/44/Logo_The_Simpsons.svg" alt="drawing" width="400"/>

## Τα δεδομένα

Θα δουλέψουμε με το σύνολο δεδομένων των σεναρίων των "The Simpsons". Αυτό το σύνολο δεδομένων περιέχει τους χαρακτήρες, τις τοποθεσίες, τις λεπτομέρειες του επεισοδίου και τις γραμμές του σεναρίου για περίπου 600 επεισόδια των Simpsons, που χρονολογούνται από το 1989. Μπορείτε να το βρείτε [εδώ](https://www.kaggle.com/ambarish/fun-in-text-mining-with-simpsons/data) (~25MB).

Κάντε το unzip. θα χρειαστούμε το simpsons_sript_lines.csv.

# Προεπεξεργασία

Θα κρατήσουμε μόνο δύο κολόνες:
* `raw_character_text`: the character who speaks (can be useful when monitoring the preprocessing steps)
* `spoken_words`: the raw text from the line of dialogue

Δενθα κρατίσουμε την κολόνα `normalized_text` γιατί θα κάνουμε τη δική μας προεπεξεργασία.

Μπορείτε να βρείτε αυτή τη μορφή του dataset [εδώ](https://www.kaggle.com/pierremegret/dialogue-lines-of-the-simpsons).

Κατεβάστε το csv και κάντε το upload στο colab από το αριστερό sidebar. Εναλλακτικά, δουλέψτε απευθείας στο Kaggle.

In [2]:
df = pd.read_csv('simpsons_script_lines.csv')
df.shape

FileNotFoundError: ignored

In [ ]:
df.head()

Οι απουσιάζουσες τιμές προέρχονται από μέρη του σεναρίου όπου συμβαίνει κάτι, αλλά χωρίς διάλογο. Για παράδειγμα "(Δημοτικό σχολείο του Σπρίνγκφιλντ: ΕΞΩΤ. ΔΗΜΟΤΙΚΌ - ΑΥΛΉ ΣΧΟΛΕΊΟΥ - ΑΠΌΓΕΥΜΑ)"

In [ ]:
df.isnull().sum()

Αφαιρούμε τις απουσιάζουσες τιμές:

In [ ]:
df = df.dropna().reset_index(drop=True)
df.isnull().sum()

## Καθαρισμός

Κάνουμε λημματοποίηση και αφαιρούμε τα stopwords και τους μη αλφαβητικούς χαρακτήρες για κάθε γραμμή διαλόγου.

In [ ]:
#nlp = spacy.load('en', disable=['ner', 'parser']) # disabling Named Entity Recognition for speed

nlp = spacy.load("en_core_web_sm", disable=['ner', 'parser']) # disabling Named Entity Recognition for speed

def cleaning(doc):
    # Lemmatizes and removes stopwords
    # doc needs to be a spacy Doc object
    txt = [token.lemma_ for token in doc if not token.is_stop]
    # Word2Vec uses context words to learn the vector representation of a target word,
    # if a sentence is only one or two words long,
    # the benefit for the training is very small
    if len(txt) > 2:
        return ' '.join(txt)

Αφαίρεση μη αλφαβητικών χαρακτήρων:

In [ ]:
brief_cleaning = (re.sub("[^A-Za-z']+", ' ', str(row)).lower() for row in df['spoken_words'])

Θα χρησιμοποιήσουμε τη μέθοδο spaCy .pipe() για να επιταχύνουμε τη διαδικασία καθαρισμού:

In [ ]:
t = time()

txt = [cleaning(doc) for doc in nlp.pipe(brief_cleaning, batch_size=5000)]

print('Time to clean up everything: {} mins'.format(round((time() - t) / 60, 2)))

Βάζουμε τα αποτελέσματα σε ένα DataFrame για να αφαιρέσουμε απουσιάζουσες τιμές και διπλές εγγραφές:

In [ ]:
df_clean = pd.DataFrame({'clean': txt})
df_clean = df_clean.dropna().drop_duplicates()
df_clean.shape

## Ν-grams
Χρησιμοποιούμε το πακέτο [Phrases](https://radimrehurek.com/gensim/models/phrases.html) του Gensim για να εξάγουμε αυτόματα συχνές φράσεις (n-grams).

Για παράδειγμα θέλουμε να μπορούμε να πιάνουμε οντότητες όπως "mr_burns" και "bart_simpson".

In [ ]:
from gensim.models.phrases import Phrases, Phraser

Επειδή το `Phrases()` λαμβάνει ως είσοδο μια λίστα λιστών:

In [ ]:
sent = [row.split() for row in df_clean['clean']]

Δημιουργούμε τις φράσεις που μας ενδιαφέρουν από τη λίστα των προτάσεων:

In [ ]:
phrases = Phrases(sent, min_count=30, progress_per=10000)

Ο στόχος της Phraser() είναι να περιορίσει τη χρήση μνήμης του Phrases(), απορρίπτοντας την κατάσταση του μοντέλου που δεν μας χρειάζεται στο συγκεκριμένο task:

In [ ]:
ngram = Phraser(phrases)

Μετατρέπουμε το σώμα κειμένου στα ngrams που έχουν ανιχνευθεί:

In [ ]:
sentences = ngram[sent]

## Πιο συχνές λέξεις:


Κυρίως ένας έλεγχος ορθότητας της αποτελεσματικότητας της λημματοποίησης, της αφαίρεσης των stopwords και της προσθήκης ngrams.

In [ ]:
word_freq = defaultdict(int)
for sent in sentences:
    for i in sent:
        word_freq[i] += 1
len(word_freq)

In [ ]:
sorted(word_freq, key=word_freq.get, reverse=True)[:10]

# Εκπαίδευση του μοντέλου
## Υλοποίηση Word2Vec της Gensim

Θα χρησιμοποιήσουμε την υλοποίηση [Word2Vec](https://radimrehurek.com/gensim/models/word2vec.html) του GenSim. 

In [ ]:
import multiprocessing

from gensim.models import Word2Vec

## Διαχωρισμός της εκπαίδευσης του μοντέλου σε 3 βήματα

Διαχωρίζουμε την εκπαίδευση σε 3 διακριτά βήματα για λόγους σαφήνειας και παρακολούθησης.
1. `Word2Vec()`: 
>Σε αυτό το πρώτο βήμα, ρυθμίζουμε τις παραμέτρους του μοντέλου μία προς μία. <br>Δεν παρέχουμε την παράμετρο `sentences`, και επομένως αφήνουμε σκόπιμα το μοντέλο μη αρχικοποιημένο.
2. `.build_vocab()`: 
>Εδώ κατασκευάζεται το λεξιλόγιο από μια ακολουθία προτάσεων και αρχικοποιείται το μοντέλο. <br>Με τα logs, μπορούμε να παρακολουθούμε την πρόοδο και, ακόμη πιο σημαντικό, την επίδραση των `min_count` και `sample` στο σώμα των λέξεων. Παρατήρούμε ότι αυτές οι δύο παράμετροι, και ειδικότερα το `sample`, έχουν μεγάλη επίδραση στην απόδοση ενός μοντέλου. Η εμφάνιση και των δύο επιτρέπει την ακριβέστερ και ευκολότερη διαχείριση της επιρροής τους.
3. `.train()`:
>Τελικά, εκπαιδεύουμε το μοντέλο.<br>
Οι καταγραφές εδώ είναι κυρίως χρήσιμες για την παρακολούθηση, διασφαλίζοντας ότι κανένα νήμα δεν εκτελείται στιγμιαία.

In [ ]:
cores = multiprocessing.cpu_count() # Count the number of cores in a computer

## Οι παράμετροι

* `min_count` <font color='purple'>=</font> <font color='green'>int</font> - Αγνοεί όλες τις λέξεις με συνολική απόλυτη συχνότητα μικρότερη από αυτή - (2, 100)


* `window` <font color='purple'>=</font> <font color='green'>int</font> - Η μέγιστη απόσταση μεταξύ της τρέχουσας και της προβλεπόμενης λέξης μέσα σε μια πρόταση. Π.χ. `παράθυρο` λέξεις στα αριστερά και `παράθυρο` λέξεις στα αριστερά του στόχου μας - (2, 10)


* `size` <font color='purple'>=</font> <font color='green'>int</font> - Διαστατικότητα των διανυσμάτων χαρακτηριστικών. - (50, 300)


* `sample` <font color='purple'>=</font> <font color='green'>float</font> - Το κατώφλι για τη διαμόρφωση των λέξεων με υψηλότερη συχνότητα που θα υποβαθμίζονται τυχαία. Έχει μεγάλη επιρροή.  - (0, 1e-5)


* `alpha` <font color='purple'>=</font> <font color='green'>float</font> - Ο αρχικός ρυθμός μάθησης - (0.01, 0.05)


* `min_alpha` <font color='purple'>=</font> <font color='green'>float</font> - Ο ρυθμός μάθησης θα πέφτει γραμμικά στο `min_alpha` καθώς η εκπαίδευση προχωράει. Για να το ορίσετε: alpha - (min_alpha * epochs) ~ 0.00


* `negative` <font color='purple'>=</font> <font color='green'>int</font> - Αν > 0, θα χρησιμοποιηθεί αρνητική δειγματοληψία, το int για το negative καθορίζει πόσες "λέξεις θορύβου" θα πρέπει να "τραβηχτούν". Αν τεθεί σε 0, δεν χρησιμοποιείται αρνητική δειγματοληψία. - (5, 20)


* `workers` <font color='purple'>=</font> <font color='green'>int</font> - Χρησιμοποιήστε τόσα νήματα εργασίας για την εκπαίδευση του μοντέλου (=γρηγορότερη εκπαίδευση με πολυπύρηνες μηχανές)

In [ ]:
w2v_model = Word2Vec(min_count=20,
                     window=2,
                     size=300,
                     sample=6e-5, 
                     alpha=0.03, 
                     min_alpha=0.0007, 
                     negative=20,
                     workers=cores-1)

## Κατασκευή του πίνακα λεξιλογίου

Το Word2Vec απαιτεί από εμάς να δημιουργήσουμε έναν πίνακα λεξιλογίου (απλά συγχωνεύοντας όλες τις λέξεις και φιλτράροντας τις μοναδικές λέξεις και κάνοντας κάποιες βασικές μετρήσεις σε αυτές):

In [ ]:
t = time()

w2v_model.build_vocab(sentences, progress_per=10000)

print('Time to build vocab: {} mins'.format(round((time() - t) / 60, 2)))

## Εκπαίδευση του μοντέλου
_Παράμετροι της εκπαίδευσης:_
* `total_examples` <font color='purple'>=</font> <font color='green'>int</font> - Πλήθος προτάσεων;
* `epochs` <font color='purple'>=</font> <font color='green'>int</font> - Πλήθος επαναλήψεων (epochs)του σώματος των κειμένων - [10, 20, 30]

In [ ]:
t = time()

w2v_model.train(sentences, total_examples=w2v_model.corpus_count, epochs=30, report_delay=1)

print('Time to train the model: {} mins'.format(round((time() - t) / 60, 2)))

Καθώς δεν σκοπεύουμε να εκπαιδεύσουμε περαιτέρω το μοντέλο, καλούμε την init_sims(), η οποία θα κάνει το μοντέλο πολύ πιο αποδοτικό στη μνήμη:

In [ ]:
w2v_model.init_sims(replace=True)

# Εξερευνώντας το μοντέλο
## Most similar

Εδώ, θα ζητήσουμε από το μοντέλο μας να βρει τη λέξη που μοιάζει περισσότερο με μερικούς από τους πιο εμβληματικούς χαρακτήρες των Simpsons.

<img src="https://vignette.wikia.nocookie.net/simpsons/images/0/02/Homer_Simpson_2006.png/revision/latest?cb=20091207194310" alt="drawing" width="130"/>

Ας δούμε τι θα πάρουμε για τον κύριο χαρακτήρα της σειράς:

In [ ]:
w2v_model.wv.most_similar(positive=["homer"])

_Μια διευκρίνιση:_<br>
Το σύνολο δεδομένων είναι οι ατάκες διαλόγου των Simpsons- επομένως, όταν εξετάζουμε τις πιο παρόμοιες λέξεις με το "homer", **δεν** είναι απαραίτητο να πάρουμε τα μέλη της οικογένειάς του, τα χαρακτηριστικά της προσωπικότητάς του ή ακόμη και τις πιο συχνές εκφράσεις του. Αντί αυτού, παίρνουμε τι είπαν άλλοι χαρακτήρες (καθώς ο Homer δεν αναφέρεται συχνά στον εαυτό του στο 3ο πρόσωπο) μαζί με το "homer", όπως πώς αισθάνεται ή φαίνεται ("depressed"), πού βρίσκεται ("hammock"), ή με ποιον   είναι ("marge").

Ας δούμε τι μας δίνει συγκριτικά το bigram "homer_simpson:

In [ ]:
w2v_model.wv.most_similar(positive=["homer_simpson"])

<img src="https://vignette.wikia.nocookie.net/simpsons/images/0/0b/Marge_Simpson.png/revision/latest?cb=20180626055729" alt="drawing" width="150"/>

Τώρα η Margie:

In [ ]:
w2v_model.wv.most_similar(positive=["marge"])

<img src="https://vignette.wikia.nocookie.net/simpsons/images/6/65/Bart_Simpson.png/revision/latest?cb=20180319061933" alt="drawing" width="100"/>

O Bart:

In [ ]:
w2v_model.wv.most_similar(positive=["bart"])

## Ομοιότητες:

Εδώ εξετάζουμε πόσο όμοιες δύο οντότητες (ngrams) μεταξύ τους:

<img src="https://vignette.wikia.nocookie.net/simpsons/images/6/6c/MaggieSimpson.PNG/revision/latest?cb=20180314210204" alt="drawing" width="100"/>

In [ ]:
w2v_model.wv.similarity('maggie', 'baby')

<img src="https://vignette.wikia.nocookie.net/simpsons/images/4/40/Picture0003.jpg/revision/latest?cb=20110623042517" alt="drawing" width="200"/>

In [ ]:
w2v_model.wv.similarity('bart', 'nelson')

## Αταίριαστη λέξη:

Εδώ ζητάμε από το μοντέλο να μας δώσει από μια λίστα την λέξη που δεν ταιριάζει!

Μεταξύ του Jimbo, του Milhouse και του Kearney, ποιος είναι αυτός που δεν είναι νταής;

In [ ]:
w2v_model.wv.doesnt_match(['jimbo', 'milhouse', 'kearney'])

<img src="https://vignette.wikia.nocookie.net/simpsons/images/9/91/Milhouse_Van_Houten_2.png/revision/latest?cb=20180429212659" alt="drawing" width="150"/>

Τι θα λέγατε αν συγκρίναμε τη φιλία μεταξύ του Nelson, του Bart, και του  Milhouse;

In [ ]:
w2v_model.wv.doesnt_match(["nelson", "bart", "milhouse"])

Τέλος, πώς είναι η σχέση μεταξύ του Όμηρου και των δύο κουνιάδων του;

In [ ]:
w2v_model.wv.doesnt_match(['homer', 'patty', 'selma'])

## Αναλογική διαφορά

Ποια λέξη είναι ως προς το woman αυτό που είναι ο homer ως προς την marge;

In [ ]:
w2v_model.wv.most_similar(positive=["woman", "homer"], negative=["marge"], topn=3)

Ποια λέξη είναι ως προς τo woman αυτό που είναι ο Bart ως προς το man;

In [ ]:
w2v_model.wv.most_similar(positive=["woman", "bart"], negative=["man"], topn=3)

<img src="https://vignette.wikia.nocookie.net/simpsons/images/5/57/Lisa_Simpson2.png/revision/latest?cb=20180319000458" alt="drawing" width="100"/>

### Οπτικοποίηση t-SNE
[Ο T-distributed Stochastic Neighbor Embedding (t-SNE)](https://scikit-learn.org/stable/modules/generated/sklearn.manifold.TSNE.html) είναι ένας μη γραμμικός αλγόριθμος μείωσης της διαστατικότητας που προσπαθεί να αναπαραστήσει δεδομένα υψηλής διάστασης και τις υποκείμενες σχέσεις μεταξύ τους σε ένα χώρο χαμηλότερης διάστασης.<br>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
 
import seaborn as sns
sns.set_style("darkgrid")

from sklearn.decomposition import PCA
from sklearn.manifold import TSNE

Ο στόχος μας σε αυτή την ενότητα είναι να σχεδιάσουμε τα διανύσματα των 300 διαστάσεων σε δισδιάστατα γραφήματα και να δούμε αν μπορούμε να εντοπίσουμε ενδιαφέροντα μοτίβα.<br>
Για το σκοπό αυτό θα χρησιμοποιήσουμε την υλοποίηση t-SNE από το scikit-learn.

Για να κάνουμε τις απεικονίσεις πιο ευδιάκριτες, θα εξετάσουμε τις σχέσεις μεταξύ μιας λέξης ερωτήματος (σε <font color='red'>**κόκκινο**</font>), των πιο παρόμοιων λέξεων της στο μοντέλο (σε <font color="blue">**μπλε**</font>) και άλλων λέξεων από το λεξιλόγιο (σε <font color='green'>**πράσινο**</font>).

In [ ]:
def tsnescatterplot(model, word, list_names, n_components=50):
    """ Plot in seaborn the results from the t-SNE dimensionality reduction algorithm of the vectors of a query word,
    its list of most similar words, and a list of words.
    """
    arrays = np.empty((0, 300), dtype='f')
    word_labels = [word]
    color_list  = ['red']

    # adds the vector of the query word
    arrays = np.append(arrays, model.wv.__getitem__([word]), axis=0)
    
    # gets list of most similar words
    close_words = model.wv.most_similar([word])
    
    # adds the vector for each of the closest words to the array
    for wrd_score in close_words:
        wrd_vector = model.wv.__getitem__([wrd_score[0]])
        word_labels.append(wrd_score[0])
        color_list.append('blue')
        arrays = np.append(arrays, wrd_vector, axis=0)
    
    # adds the vector for each of the words from list_names to the array
    for wrd in list_names:
        wrd_vector = model.wv.__getitem__([wrd])
        word_labels.append(wrd)
        color_list.append('green')
        arrays = np.append(arrays, wrd_vector, axis=0)
        
    # Reduces the dimensionality from 300 to 50 dimensions with PCA
    reduc = PCA(n_components).fit_transform(arrays)
    
    # Finds t-SNE coordinates for 2 dimensions
    np.set_printoptions(suppress=True)
    
    Y = TSNE(n_components=2, random_state=0, perplexity=15).fit_transform(reduc)
    
    # Sets everything up to plot
    df = pd.DataFrame({'x': [x for x in Y[:, 0]],
                       'y': [y for y in Y[:, 1]],
                       'words': word_labels,
                       'color': color_list})
    
    fig, _ = plt.subplots()
    fig.set_size_inches(9, 9)
    
    # Basic plot
    p1 = sns.regplot(data=df,
                     x="x",
                     y="y",
                     fit_reg=False,
                     marker="o",
                     scatter_kws={'s': 40,
                                  'facecolors': df['color']
                                 }
                    )
    
    # Adds annotations one by one with a loop
    for line in range(0, df.shape[0]):
         p1.text(df["x"][line],
                 df['y'][line],
                 '  ' + df["words"][line].title(),
                 horizontalalignment='left',
                 verticalalignment='bottom', size='medium',
                 color=df['color'][line],
                 weight='normal'
                ).set_size(15)

    
    plt.xlim(Y[:, 0].min()-50, Y[:, 0].max()+50)
    plt.ylim(Y[:, 1].min()-50, Y[:, 1].max()+50)
            
    plt.title('t-SNE visualization for {}'.format(word.title()))
    

## 10 πιο παρόμοιες λέξεις έναντι 8 τυχαίων λέξεων

Ας συγκρίνουμε πού βρίσκεται η διανυσματική αναπαράσταση του homer, των 10 πιο παρόμοιων λέξεων του από το μοντέλο, καθώς και 8 τυχαίων λέξεων, σε ένα δισδιάστατο γράφημα:

In [ ]:
tsnescatterplot(w2v_model, 'homer', ['dog', 'bird', 'ah', 'maude', 'bob', 'mel', 'apu', 'duff'], n_components=8)

## 10 πιο παρόμοιες λέξεις vs. 10 πιο ανόμοιες

Αυτή τη φορά, ας συγκρίνουμε πού βρίσκεται η διανυσματική αναπαράσταση της Maggie και των 10 πιο όμοιων λέξεων της από το μοντέλο σε σύγκριση με τη διανυσματική αναπαράσταση των 10 πιο ανόμοιων λέξεων με τη Maggie:

In [ ]:
tsnescatterplot(w2v_model, 'maggie', [i[0] for i in w2v_model.wv.most_similar(negative=["maggie"])], n_components=10)

## 10 πιο παρόμοιες λέξεις vs. 11η έως 20η πιο παρόμοιες λέξεις

Τέλος, θα παρουσιάσουμε τις πιο παρόμοιες λέξεις με τον κ. Burns που κατατάσσονται από την 1η έως τη 10η θέση σε σχέση με αυτές που κατατάσσονται από την 11η έως την 20η θέση:

In [ ]:
tsnescatterplot(w2v_model, "mr_burn", [t[0] for t in w2v_model.wv.most_similar(positive=["mr_burn"], topn=20)][10:],  n_components=10)

<img src="https://upload.wikimedia.org/wikipedia/en/5/56/Mr_Burns.png" alt="drawing"  width="200"/>